In [ ]:
# pip install basemap


In [1]:
import os
import sys
import pandas as pd
import numpy as np
import obspy
from tqdm import tqdm

from obspy.clients.fdsn import Client
from obspy.clients.fdsn import Client as FDSNClient

from mpl_toolkits.basemap import Basemap


from pnwstore.mseed import WaveformClient
from datetime import datetime
from matplotlib import pyplot as plt
from matplotlib.backends.backend_pdf import PdfPages

from obspy import UTCDateTime

from tqdm import tqdm
from obspy.geodetics import locations2degrees, degrees2kilometers

notebook_dir = os.getcwd()
parent_dir = os.path.abspath(os.path.join(notebook_dir, '../'))
if parent_dir not in sys.path:
    sys.path.append(parent_dir)
    
from plot_utils import *
from qc_utils import * 

## Morton Catalog

In [2]:
# Read Morton's catalog
events_morton = pd.read_csv('../data/ds01.csv')
# Convert the TSTRING to datetime
events_morton['datetime'] = pd.to_datetime(events_morton['TSTRING'], format='%Y%m%d%H%M%S', utc=True)
# Get the events in the Morton catalog 
t1 = pd.Timestamp('2011-1-1 00:00:00.000000+0000', tz='UTC')
t2 = pd.Timestamp('2015-12-31 23:59:59.999999+0000', tz='UTC')

events_morton= events_morton.loc[(events_morton['datetime'] > t1) & (events_morton['datetime'] < t2) ]

events_morton.head()

CI YEAR       TSTRING    YEAR  MONTH   DAY  HOUR  MINUTE  SECOND      LAT  \
0      1.0  2.011073e+13  2011.0    7.0  26.0   1.0     2.0    7.37  47.3217   
1      1.0  2.011073e+13  2011.0    7.0  26.0   1.0     2.0    7.72  44.2888   
2      1.0  2.011073e+13  2011.0    7.0  26.0   1.0     2.0    8.56  44.3017   
3      1.0  2.011073e+13  2011.0    7.0  26.0   7.0    31.0    2.17  48.2635   
4      1.0  2.011073e+13  2011.0    7.0  26.0   9.0    50.0   27.63  48.3032   

        LON  ...  dist to nearest stn  tt RMS   ERH   ERZ  STRIKE  DIP  RAKE  \
0 -123.2708  ...                 27.4    0.19   0.8   1.2     NaN  NaN   NaN   
1 -124.3340  ...                163.8    0.06  13.1   3.2     NaN  NaN   NaN   
2 -124.3180  ...                131.1    0.50  35.4  22.2     NaN  NaN   NaN   
3 -124.9298  ...                 44.4    0.77   3.5   6.4     NaN  NaN   NaN   
4 -124.9157  ...                 46.1    0.94   4.0   6.9     NaN  NaN   NaN   

   PLATE DESIGNATION  TEMPLATE EVENT?                  datetime  
0          Interface          Catalog 2011-07-26 01:02:07+00:00  
1        Upper Plate              NaN 2011-07-26 01:02:07+00:00  
2        Upper Plate              NaN 2011-07-26 01:02:08+00:00  
3        Upper Plate              NaN 2011-07-26 07:31:02+00:00  
4        Upper Plate                T 2011-07-26 09:50:27+00:00  

[5 rows x 24 columns]

In [3]:
events_morton

CI YEAR       TSTRING    YEAR  MONTH   DAY  HOUR  MINUTE  SECOND  \
0         1.0  2.011073e+13  2011.0    7.0  26.0   1.0     2.0    7.37   
1         1.0  2.011073e+13  2011.0    7.0  26.0   1.0     2.0    7.72   
2         1.0  2.011073e+13  2011.0    7.0  26.0   1.0     2.0    8.56   
3         1.0  2.011073e+13  2011.0    7.0  26.0   7.0    31.0    2.17   
4         1.0  2.011073e+13  2011.0    7.0  26.0   9.0    50.0   27.63   
...       ...           ...     ...    ...   ...   ...     ...     ...   
5277      4.0  2.015101e+13  2015.0   10.0   7.0   8.0     1.0   50.83   
5278      4.0  2.015101e+13  2015.0   10.0   7.0   8.0     7.0    8.40   
5279      4.0  2.015101e+13  2015.0   10.0   7.0  11.0    31.0   26.69   
5280      4.0  2.015101e+13  2015.0   10.0   7.0  18.0    11.0    9.52   
5281      4.0  2.015101e+13  2015.0   10.0   7.0  21.0    45.0   50.37   

          LAT       LON  ...  dist to nearest stn  tt RMS   ERH   ERZ  STRIKE  \
0     47.3217 -123.2708  ...                 27.4    0.19   0.8   1.2     NaN   
1     44.2888 -124.3340  ...                163.8    0.06  13.1   3.2     NaN   
2     44.3017 -124.3180  ...                131.1    0.50  35.4  22.2     NaN   
3     48.2635 -124.9298  ...                 44.4    0.77   3.5   6.4     NaN   
4     48.3032 -124.9157  ...                 46.1    0.94   4.0   6.9     NaN   
...       ...       ...  ...                  ...     ...   ...   ...     ...   
5277  40.5895 -124.0455  ...                  5.4    0.14   0.9   0.8     NaN   
5278  40.5380 -123.7217  ...                 14.9    0.09   3.3  13.5     NaN   
5279  40.5822 -124.0432  ...                  5.6    0.05   1.7   0.8     NaN   
5280  40.2710 -124.3777  ...                  7.9    0.19   0.7   0.2     NaN   
5281  40.1602 -123.8320  ...                 29.4    0.22   1.3  18.6     NaN   

      DIP  RAKE  PLATE DESIGNATION  TEMPLATE EVENT?                  datetime  
0     NaN   NaN          Interface          Catalog 2011-07-26 01:02:07+00:00  
1     NaN   NaN        Upper Plate              NaN 2011-07-26 01:02:07+00:00  
2     NaN   NaN        Upper Plate              NaN 2011-07-26 01:02:08+00:00  
3     NaN   NaN        Upper Plate              NaN 2011-07-26 07:31:02+00:00  
4     NaN   NaN        Upper Plate                T 2011-07-26 09:50:27+00:00  
...   ...   ...                ...              ...                       ...  
5277  NaN   NaN               Slab              NaN 2015-10-07 08:01:50+00:00  
5278  NaN   NaN        Upper Plate              NaN 2015-10-07 08:07:08+00:00  
5279  NaN   NaN               Slab              NaN 2015-10-07 11:31:26+00:00  
5280  NaN   NaN        Upper Plate              NaN 2015-10-07 18:11:09+00:00  
5281  NaN   NaN              Undef              NaN 2015-10-07 21:45:50+00:00  

[5282 rows x 24 columns]

## ANSS Catalog

In [4]:
events_anss = pd.read_csv('../data/anss_2011-15.csv')
events_anss['datetime'] = pd.to_datetime(events_anss['time'], format='%Y-%m-%dT%H:%M:%S.%fZ', utc=True)
events_anss= events_anss.loc[(events_anss['datetime'] > t1) & (events_anss['datetime'] < t2) ]
events_anss

time   latitude   longitude   depth   mag magType  \
0     2015-12-30T15:14:18.870Z  40.663500 -124.371333  31.190  2.65      md   
1     2015-12-30T14:56:15.320Z  43.313800 -126.770100  10.000  3.20      ml   
2     2015-12-30T07:39:29.310Z  48.586500 -123.300333  52.420  4.79      ml   
3     2015-12-29T21:21:55.820Z  40.604667 -124.427500  28.360  2.84      ml   
4     2015-12-29T07:33:12.890Z  48.915500 -125.569000  33.970  1.82      ml   
...                        ...        ...         ...     ...   ...     ...   
4180  2011-01-04T11:32:14.540Z  40.305000 -124.599000  20.290  2.53      md   
4181  2011-01-03T07:49:17.260Z  40.405333 -123.799667  29.414  2.80      ml   
4182  2011-01-02T22:40:11.410Z  40.315667 -124.593500  17.310  3.79      ml   
4183  2011-01-02T06:00:27.060Z  40.451167 -125.909333  22.647  3.68      ml   
4184  2011-01-01T10:44:25.620Z  40.318333 -124.467167  19.780  2.33      md   

       nst    gap     dmin   rms  ...                                  place  \
0     18.0  215.0  0.11980  0.08  ...  near the coast of Northern California   
1      NaN  196.0  1.83800  0.73  ...                off the coast of Oregon   
2     27.0   81.0  0.11670  0.19  ...      12 km SE of North Saanich, Canada   
3     23.0  228.0  0.12790  0.08  ...      14 km WNW of Ferndale, California   
4      4.0  313.0  0.02003  0.10  ...           3 km SSW of Ucluelet, Canada   
...    ...    ...      ...   ...  ...                                    ...   
4180  23.0  241.0  0.22970  0.09  ...       41 km SW of Ferndale, California   
4181  24.0   42.0  0.02613  0.15  ...        12 km E of Redcrest, California   
4182  35.0  241.0  0.22880  0.19  ...       40 km SW of Ferndale, California   
4183  34.0  275.0  1.24000  0.26  ...       140 km W of Ferndale, California   
4184  14.0  301.0  0.13960  0.28  ...      33 km SSW of Ferndale, California   

            type horizontalError depthError magError  magNst    status  \
0     earthquake            0.88       0.87    0.204    41.0  reviewed   
1     earthquake            8.70       2.00    0.056    42.0  reviewed   
2     earthquake            0.43       0.67    0.137   178.0  reviewed   
3     earthquake            0.75       0.51    0.270    19.0  reviewed   
4     earthquake            1.23       0.78    0.210     3.0  reviewed   
...          ...             ...        ...      ...     ...       ...   
4180  earthquake            0.51       0.24    0.211    31.0  reviewed   
4181  earthquake            0.39       0.87    0.151    15.0  reviewed   
4182  earthquake            0.88       0.43    0.198    36.0  reviewed   
4183  earthquake            3.55      14.43    0.357    12.0  reviewed   
4184  earthquake            1.62       0.63    0.263    13.0  reviewed   

      locationSource  magSource                         datetime  
0                 nc         nc 2015-12-30 15:14:18.870000+00:00  
1                 us         us 2015-12-30 14:56:15.320000+00:00  
2                 uw         uw 2015-12-30 07:39:29.310000+00:00  
3                 nc         nc 2015-12-29 21:21:55.820000+00:00  
4                 uw         uw 2015-12-29 07:33:12.890000+00:00  
...              ...        ...                              ...  
4180              nc         nc 2011-01-04 11:32:14.540000+00:00  
4181              nc         nc 2011-01-03 07:49:17.260000+00:00  
4182              nc         nc 2011-01-02 22:40:11.410000+00:00  
4183              nc         nc 2011-01-02 06:00:27.060000+00:00  
4184              nc         nc 2011-01-01 10:44:25.620000+00:00  

[4185 rows x 23 columns]

## Our Catalog

In [5]:
# Load all the pick assignments 
mycatalog_picks = pd.read_csv('../data/datasets_pnsn_jdf/all_pick_assignments_pnsn_jdf.csv')
mycatalog = mycatalog_picks.drop_duplicates(subset=['idx'])
# Convert the time series in all_pick_assignments to datetime
mycatalog['datetime'] = pd.to_datetime(mycatalog['time'], utc = True)
mycatalog=mycatalog.loc[(mycatalog['datetime'] > t1) & (mycatalog['datetime'] < t2) ]
mycatalog

/tmp/ipykernel_1409532/766234642.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  mycatalog['datetime'] = pd.to_datetime(mycatalog['time'], utc = True)


Unnamed: 0    idx                              time           x  \
0                0      1  2011-12-10 22:44:45.831192+00:00  -96.868991   
6                6      2  2011-12-26 18:06:14.336595+00:00   -8.037165   
13              13      7  2012-02-04 20:05:31.203164+00:00 -200.083112   
20              20      8  2012-02-06 08:17:12.359449+00:00  -67.258382   
26              26     11  2012-02-16 06:37:34.356357+00:00   68.950417   
...            ...    ...                               ...         ...   
175263      175263  31062  2015-09-14 05:33:02.400734+00:00  -57.952191   
175271      175271  31063  2015-09-14 06:09:08.330498+00:00 -145.091982   
175281      175281  31064  2015-09-14 13:34:01.190085+00:00 -161.166312   
175290      175290  31068  2015-09-15 09:12:53.198694+00:00 -148.476051   
175296      175296  31069  2015-09-15 17:31:03.343072+00:00   68.950417   

                 y          z  picks   latitude   longitude      depth  \
0        57.435553  12.890625      6  45.010235 -126.728790  12.890625   
6       129.232778   0.390625      7  45.662816 -125.603130   0.390625   
13      484.629041  49.609375      7  48.827345 -128.225159  49.609375   
20     -124.450749   3.515625      6  43.376931 -126.329931   3.515625   
26      488.218902  49.609375      6  48.888012 -124.559792  49.609375   
...            ...        ...    ...        ...         ...        ...   
175263 -367.364693   0.390625      8  41.191011 -126.190794   0.390625   
175271 -447.538261  49.609375     10  40.458469 -127.210546  49.609375   
175281 -434.375436  49.609375      9  40.573981 -127.403307  49.609375   
175290 -277.618162   1.171875      6  41.987149 -127.291699   1.171875   
175296 -466.684187  49.609375      6  40.295865 -124.689054  49.609375   

        event_idx  pick_idx  residual station phase     time_pick  \
0               1   1655834  0.594705    J35A     P  1.323557e+09   
6               2   1654163 -0.086003    J35A     P  1.324923e+09   
13              7    345847 -1.237492    J35A     P  1.328386e+09   
20              8    121103 -0.180289    J35A     P  1.328516e+09   
26             11     87298 -0.443887    J35A     P  1.329374e+09   
...           ...       ...       ...     ...   ...           ...   
175263      31062   1476568 -0.072230    G10D     P  1.442209e+09   
175271      31063   1476574 -0.554440    G10D     P  1.442211e+09   
175281      31064   1476584  0.269303    G10D     P  1.442238e+09   
175290      31068   1452051  0.333196    G10D     P  1.442308e+09   
175296      31069   1452085  0.041425    G10D     P  1.442338e+09   

                               datetime  
0      2011-12-10 22:44:45.831192+00:00  
6      2011-12-26 18:06:14.336595+00:00  
13     2012-02-04 20:05:31.203164+00:00  
20     2012-02-06 08:17:12.359449+00:00  
26     2012-02-16 06:37:34.356357+00:00  
...                                 ...  
175263 2015-09-14 05:33:02.400734+00:00  
175271 2015-09-14 06:09:08.330498+00:00  
175281 2015-09-14 13:34:01.190085+00:00  
175290 2015-09-15 09:12:53.198694+00:00  
175296 2015-09-15 17:31:03.343072+00:00  

[19036 rows x 17 columns]

## Run this loop

In [6]:
matched_events_mycatalog2morton = []
matched_times_morton2mycatalog = []
matched_events_morton2mycatalog = []
unmatched_times_morton2mycatalog = []
unmatched_events_morton2mycatalog = []
unmatched_events_mycatalog2morton_and_anss = []
matched_events_anss2mycatalog=[]
matched_events_mycatalog2anss = []
unmatched_times_anss2mycatalog = []
unmatched_events_anss2mycatalog = []
matched_times_anss2mycatalog =[]

time_threshold = 5 # in seconds
dist_threshold =25

lat_morton2mycatalog = []
lon_morton2mycatalog = []

lat_anss2mycatalog =[]
lon_anss2mycatalog = []

# A set to keep track of matched indices in mycatalog
matched_indices_morton = set()
matched_indices_anss = set()
count_c = 0
count_d = 0
# Loop over events in Morton's catalog
for i in range(len(events_morton)):
    t11 = events_morton.iloc[i]['datetime']
    olat = events_morton.iloc[i]['LAT']
    olon = events_morton.iloc[i]['LON']
    
    
    
    condition = (mycatalog['datetime'] >= t11 - pd.Timedelta(seconds=time_threshold)) & \
                     (mycatalog['datetime'] <= t11 + pd.Timedelta(seconds=time_threshold)) & \
                     (degrees2kilometers(locations2degrees(olat, olon, mycatalog['latitude'], mycatalog['longitude'])) <= dist_threshold)                        
    matched_df = mycatalog.loc[condition]

    if len(matched_df) == 1:
        print('matched idx of Morton: ',i)
        count_c+=1
        matched_times_morton2mycatalog.append(t11)
        matched_events_morton2mycatalog.append(events_morton.iloc[i])
        lat_morton2mycatalog.append(events_morton.iloc[i]['LAT'])
        lon_morton2mycatalog.append(events_morton.iloc[i]['LON'])
        matched_events_mycatalog2morton.append(matched_df)
        matched_indices_morton.update(matched_df['idx'])
    elif len(matched_df) > 1:
        print('matched idx of Morton: ',i)

        count_d+=1
        diffs = abs(matched_df['datetime'] - t11)
        closest_index = diffs.idxmin()
        closest_event = matched_df.loc[[closest_index]]
        matched_times_morton2mycatalog.append(t11)
        matched_events_morton2mycatalog.append(events_morton.iloc[i])
        lat_morton2mycatalog.append(events_morton.iloc[i]['LAT'])
        lon_morton2mycatalog.append(events_morton.iloc[i]['LON'])
        matched_events_mycatalog2morton.append(closest_event)
        matched_indices_morton.update(closest_event['idx'])
    else:
        unmatched_times_morton2mycatalog.append(t11)
        unmatched_events_morton2mycatalog.append(events_morton.iloc[i])

# All events in mycatalog not matched with Morton's catalog are unmatched
unmatched_indices_morton = set(mycatalog.idx) - matched_indices_morton
# unmatched_events_mycatalog2morton = mycatalog.iloc[list(unmatched_indices_morton)]
count_a =0
count_b =0
# Loop over events in ANSS catalog
for i in range(len(events_anss)):
    t11 = events_anss.iloc[i]['datetime']
    time_condition = (mycatalog['datetime'] >= t11 - pd.Timedelta(seconds=time_threshold)) & \
                     (mycatalog['datetime'] <= t11 + pd.Timedelta(seconds=time_threshold))
    matched_df = mycatalog.loc[time_condition]
    
    if len(matched_df) == 1:
        
        count_a+=1
        matched_times_anss2mycatalog.append(t11)
        matched_events_anss2mycatalog.append(events_anss.iloc[i])
        lat_anss2mycatalog.append(events_anss.iloc[i]['latitude'])
        lon_anss2mycatalog.append(events_anss.iloc[i]['longitude'])
        matched_events_mycatalog2anss.append(matched_df)
        matched_indices_anss.update(matched_df['idx'])
        
    elif len(matched_df) > 1:
        count_b+=1
        diffs = abs(matched_df['datetime'] - t11)
        closest_index = diffs.idxmin()
        closest_event = matched_df.loc[[closest_index]]
        matched_times_anss2mycatalog.append(t11)
        matched_events_anss2mycatalog.append(events_anss.iloc[i])
        lat_anss2mycatalog.append(events_anss.iloc[i]['latitude'])
        lon_anss2mycatalog.append(events_anss.iloc[i]['longitude'])
        matched_events_mycatalog2anss.append(closest_event)
        matched_indices_anss.update(closest_event['idx'])
        
    else:
        unmatched_times_anss2mycatalog.append(t11)
        unmatched_events_anss2mycatalog.append(events_anss.iloc[i])

# All events in mycatalog not matched with ANSS catalog are unmatched
unmatched_indices_anss = set(mycatalog.idx) - matched_indices_anss

unmatched_indices_morton_and_anss = unmatched_indices_morton.intersection(unmatched_indices_anss)
print(len(mycatalog),len(unmatched_indices_morton_and_anss))

# unmatched_events_mycatalog2morton_and_anss = mycatalog.iloc[list(unmatched_indices_morton_and_anss)]
unmatched_events_mycatalog2morton_and_anss = mycatalog.loc[mycatalog['event_idx'].isin(list(unmatched_indices_morton_and_anss))]


print(f"length of mycatalog:{len(mycatalog)}")
print(f"length of events_morton:{len(events_morton)}")
print(f"length of events_anss:{len(events_anss)}")
print(f"matched_indices_morton:{len(matched_indices_morton)}")
print(f"matched_indices_anss:{len(matched_indices_anss)}")
print(f"unmatched_indices_morton:{len(unmatched_indices_morton)}")
print(f"unmatched_indices_anss:{len(unmatched_indices_anss)}")
print(f"unmatched_indices_morton_and_anss (new events):{len(unmatched_indices_morton_and_anss)}")



matched idx of Morton:  284
matched idx of Morton:  499
matched idx of Morton:  504
matched idx of Morton:  510
matched idx of Morton:  511
matched idx of Morton:  512
matched idx of Morton:  513
matched idx of Morton:  521
matched idx of Morton:  522
matched idx of Morton:  523
matched idx of Morton:  526
matched idx of Morton:  529
matched idx of Morton:  531
matched idx of Morton:  533
matched idx of Morton:  535
matched idx of Morton:  536
matched idx of Morton:  537
matched idx of Morton:  543
matched idx of Morton:  545
matched idx of Morton:  546
matched idx of Morton:  547
matched idx of Morton:  548
matched idx of Morton:  549
matched idx of Morton:  550
matched idx of Morton:  553
matched idx of Morton:  556
matched idx of Morton:  557
matched idx of Morton:  559
matched idx of Morton:  560
matched idx of Morton:  561
matched idx of Morton:  562
matched idx of Morton:  565
matched idx of Morton:  566
matched idx of Morton:  567
matched idx of Morton:  568
matched idx of Morto

matched idx of Morton:  2061
matched idx of Morton:  2062
matched idx of Morton:  2063
matched idx of Morton:  2064
matched idx of Morton:  2065
matched idx of Morton:  2069
matched idx of Morton:  2070
matched idx of Morton:  2071
matched idx of Morton:  2076
matched idx of Morton:  2077
matched idx of Morton:  2081
matched idx of Morton:  2093
matched idx of Morton:  2096
matched idx of Morton:  2097
matched idx of Morton:  2098
matched idx of Morton:  2104
matched idx of Morton:  2106
matched idx of Morton:  2108
matched idx of Morton:  2109
matched idx of Morton:  2113
matched idx of Morton:  2118
matched idx of Morton:  2121
matched idx of Morton:  2122
matched idx of Morton:  2126
matched idx of Morton:  2128
matched idx of Morton:  2133
matched idx of Morton:  2134
matched idx of Morton:  2136
matched idx of Morton:  2138
matched idx of Morton:  2142
matched idx of Morton:  2147
matched idx of Morton:  2148
matched idx of Morton:  2153
matched idx of Morton:  2154
matched idx of

matched idx of Morton:  2821
matched idx of Morton:  2823
matched idx of Morton:  2824
matched idx of Morton:  2828
matched idx of Morton:  2835
matched idx of Morton:  2836
matched idx of Morton:  2837
matched idx of Morton:  2838
matched idx of Morton:  2843
matched idx of Morton:  2846
matched idx of Morton:  2847
matched idx of Morton:  2848
matched idx of Morton:  2852
matched idx of Morton:  2854
matched idx of Morton:  2855
matched idx of Morton:  2857
matched idx of Morton:  2859
matched idx of Morton:  2862
matched idx of Morton:  2865
matched idx of Morton:  2866
matched idx of Morton:  2871
matched idx of Morton:  2872
matched idx of Morton:  2875
matched idx of Morton:  2877
matched idx of Morton:  2878
matched idx of Morton:  2881
matched idx of Morton:  2882
matched idx of Morton:  2883
matched idx of Morton:  2888
matched idx of Morton:  2889
matched idx of Morton:  2890
matched idx of Morton:  2891
matched idx of Morton:  2895
matched idx of Morton:  2897
matched idx of

matched idx of Morton:  3555
matched idx of Morton:  3556
matched idx of Morton:  3557
matched idx of Morton:  3560
matched idx of Morton:  3563
matched idx of Morton:  3564
matched idx of Morton:  3565
matched idx of Morton:  3567
matched idx of Morton:  3574
matched idx of Morton:  3576
matched idx of Morton:  3583
matched idx of Morton:  3585
matched idx of Morton:  3586
matched idx of Morton:  3589
matched idx of Morton:  3595
matched idx of Morton:  3596
matched idx of Morton:  3598
matched idx of Morton:  3599
matched idx of Morton:  3601
matched idx of Morton:  3603
matched idx of Morton:  3607
matched idx of Morton:  3615
matched idx of Morton:  3616
matched idx of Morton:  3618
matched idx of Morton:  3623
matched idx of Morton:  3628
matched idx of Morton:  3639
matched idx of Morton:  3641
matched idx of Morton:  3643
matched idx of Morton:  3645
matched idx of Morton:  3649
matched idx of Morton:  3650
matched idx of Morton:  3651
matched idx of Morton:  3659
matched idx of

matched idx of Morton:  4441
matched idx of Morton:  4451
matched idx of Morton:  4452
matched idx of Morton:  4459
matched idx of Morton:  4460
matched idx of Morton:  4461
matched idx of Morton:  4462
matched idx of Morton:  4463
matched idx of Morton:  4468
matched idx of Morton:  4469
matched idx of Morton:  4470
matched idx of Morton:  4471
matched idx of Morton:  4476
matched idx of Morton:  4478
matched idx of Morton:  4481
matched idx of Morton:  4485
matched idx of Morton:  4486
matched idx of Morton:  4490
matched idx of Morton:  4491
matched idx of Morton:  4492
matched idx of Morton:  4494
matched idx of Morton:  4503
matched idx of Morton:  4505
matched idx of Morton:  4507
matched idx of Morton:  4508
matched idx of Morton:  4510
matched idx of Morton:  4515
matched idx of Morton:  4518
matched idx of Morton:  4519
matched idx of Morton:  4521
matched idx of Morton:  4522
matched idx of Morton:  4523
matched idx of Morton:  4526
matched idx of Morton:  4528
matched idx of

In [32]:
t11 = events_morton.iloc[0]['datetime']
olat = events_morton.iloc[3152]['LAT']
olon = events_morton.iloc[3152]['LON']

condition = (mycatalog['datetime'] >= t11 - pd.Timedelta(seconds=time_threshold)) & \
                 (mycatalog['datetime'] <= t11 + pd.Timedelta(seconds=time_threshold)) & \
                 (degrees2kilometers(locations2degrees(olat, olon, mycatalog['latitude'], mycatalog['longitude'])) <= dist_threshold)
condition

0         False
6         False
13        False
20        False
26        False
          ...  
175263    False
175271    False
175281    False
175290    False
175296    False
Name: datetime, Length: 19036, dtype: bool

In [33]:
for i in condition:
    if i == True:
        print('Index of True: ',i)

In [19]:
matched_indices_morton

{21,
 34,
 41,
 16431,
 50,
 53,
 56,
 57,
 70,
 71,
 24648,
 24650,
 76,
 16462,
 16469,
 90,
 24669,
 16478,
 99,
 114,
 24699,
 130,
 16521,
 16524,
 24717,
 142,
 16527,
 150,
 151,
 24742,
 16568,
 16580,
 24775,
 24781,
 16599,
 24794,
 24800,
 233,
 254,
 256,
 24840,
 24842,
 16652,
 275,
 24855,
 280,
 284,
 16672,
 24869,
 24874,
 306,
 312,
 16696,
 16708,
 330,
 24911,
 24912,
 16722,
 16723,
 24921,
 350,
 24926,
 353,
 16741,
 362,
 24939,
 24941,
 367,
 24943,
 24944,
 373,
 385,
 386,
 388,
 16780,
 16783,
 400,
 16788,
 405,
 24986,
 411,
 16798,
 16801,
 420,
 421,
 425,
 25020,
 25021,
 472,
 16861,
 25056,
 16870,
 16871,
 493,
 25071,
 496,
 498,
 510,
 16902,
 519,
 520,
 16910,
 16933,
 16943,
 25144,
 569,
 16958,
 25152,
 25156,
 588,
 16974,
 594,
 602,
 603,
 611,
 612,
 17000,
 639,
 25215,
 644,
 25220,
 25226,
 652,
 17050,
 25245,
 25246,
 17059,
 676,
 25252,
 680,
 17067,
 17075,
 25294,
 17153,
 17167,
 17171,
 17176,
 25381,
 25387,
 17199,
 25392,
 1

In [7]:
# new concat code
# Concatenate and clean up dataframes
if len(matched_events_mycatalog2morton)>0:
    matched_events_mycatalog2morton = pd.concat(matched_events_mycatalog2morton).reset_index(drop=True)
    matched_times_mycatalog2morton = matched_events_mycatalog2morton['datetime']
    lat_mycatalog2morton = matched_events_mycatalog2morton['latitude']
    lon_mycatalog2morton = matched_events_mycatalog2morton['longitude']

if len(matched_events_morton2mycatalog)>0:   
    matched_events_morton2mycatalog = pd.DataFrame(matched_events_morton2mycatalog).reset_index(drop=True)
    
if len(unmatched_events_anss2mycatalog)>0:
    unmatched_events_anss2mycatalog = pd.DataFrame(unmatched_events_anss2mycatalog).reset_index(drop=True)
    
if len(unmatched_events_morton2mycatalog)>0:
    unmatched_events_morton2mycatalog = pd.DataFrame(unmatched_events_morton2mycatalog).reset_index(drop=True)

if len(unmatched_events_mycatalog2morton_and_anss) > 0:
    unmatched_events_mycatalog2morton_and_anss = unmatched_events_mycatalog2morton_and_anss.reset_index(drop=True)

if len(matched_events_mycatalog2anss)>0:
    matched_events_mycatalog2anss = pd.concat(matched_events_mycatalog2anss).reset_index(drop=True)
    matched_times_mycatalog2anss = matched_events_mycatalog2anss['datetime']
    lat_mycatalog2anss = matched_events_mycatalog2anss['latitude']
    lon_mycatalog2anss = matched_events_mycatalog2anss['longitude']

if len(matched_events_anss2mycatalog)>0:   
    matched_events_anss2mycatalog = pd.DataFrame(matched_events_anss2mycatalog).reset_index(drop=True)
    matched_times_anss2mycatalog = matched_events_anss2mycatalog['datetime']

print(f"length of mycatalog:{len(mycatalog)}")
print(f"length of events_morton:{len(events_morton)}")
print(f"length of events_anss:{len(events_anss)}")
print(f"matched_events_mycatalog2morton:{len(matched_events_mycatalog2morton)}")
print(f"matched_events_morton2mycatalog:{len(matched_events_morton2mycatalog)}")
print(f"unmatched_events_anss2mycatalog:{len(unmatched_events_anss2mycatalog)}")
print(f"unmatched_events_morton2mycatalog:{len(unmatched_events_morton2mycatalog)}")
print(f"unmatched_events_mycatalog2morton_and_anss (new events):{len(unmatched_events_mycatalog2morton_and_anss)}")
print(f"matched_events_mycatalog2anss:{len(matched_events_mycatalog2anss)}")
print(f"matched_events_anss2mycatalog:{len(matched_events_anss2mycatalog)}")

length of mycatalog:19036
length of events_morton:5282
length of events_anss:4185
matched_events_mycatalog2morton:1395
matched_events_morton2mycatalog:1395
unmatched_events_anss2mycatalog:3092
unmatched_events_morton2mycatalog:3887
unmatched_events_mycatalog2morton_and_anss (new events):16978
matched_events_mycatalog2anss:1093
matched_events_anss2mycatalog:1093


In [8]:
# Save these three catalogs to csv files
matched_events_mycatalog2morton.to_csv('../data/datasets_pnsn_jdf/matched_events_with_morton_mycatalog.csv')
matched_events_anss2mycatalog.to_csv('../data/datasets_pnsn_jdf/matched_events_with_mycatalog_anss.csv')
matched_events_morton2mycatalog.to_csv('../data/datasets_pnsn_jdf/matched_events_with_mycatalog_morton.csv')
unmatched_events_mycatalog2morton_and_anss.to_csv('../data/datasets_pnsn_jdf/new_events.csv')
matched_events_mycatalog2anss.to_csv('../data/datasets_pnsn_jdf/matched_events_with_anss_mycatalog.csv')
unmatched_events_morton2mycatalog.to_csv('../data/datasets_pnsn_jdf/missing_events_from_mycatalog_morton.csv')
unmatched_events_anss2mycatalog.to_csv('../data/datasets_pnsn_jdf/missing_events_from_mycatalog_anss.csv')


## Plot the Origin Times

### Compare with Morton's Catalog 

In [ ]:
# Make lists for plotting the 1:1 line
x = pd.date_range(start='2011-1-1', end='2015-12-31', periods=len(matched_times_morton2mycatalog))
y = pd.date_range(start='2011-1-1', end='2015-12-31', periods=len(matched_times_morton2mycatalog))

# Plot the scatter plot
plt.figure()
plt.scatter(matched_times_mycatalog2morton,matched_times_morton2mycatalog)
plt.plot(x,y, 'k--')
plt.xlabel('Origin Time of mycatalog')
plt.ylabel('Origin Time of Morton')
plt.title('Scatter Plot: Origin Times of Matched Events')

### Compare with the ANSS Catalog 

In [ ]:
# Make lists for plotting the 1:1 line
matched_times_mycatalog2anss = pd.to_datetime(matched_times_mycatalog2anss)
matched_times_anss2mycatalog = pd.to_datetime(matched_times_anss2mycatalog)

x = pd.date_range(start='2014-1-1', end='2014-12-31', periods=len(matched_times_anss2mycatalog))
y = pd.date_range(start='2014-1-1', end='2014-12-31', periods=len(matched_times_anss2mycatalog))

# Plot the scatter plot
plt.figure()
plt.scatter(matched_times_mycatalog2anss,matched_times_anss2mycatalog)
plt.plot(x,y, 'k--')
plt.xlabel('Origin Time of mycatalog')
plt.ylabel('Origin Time of Morton')
plt.title('Scatter Plot: Origin Times of Matched Events')

## Plot the Latitudes

### Compare with Morton's Catalog 

In [ ]:
# Plot the scatter plot
plt.figure()
lat_min = min(lat_mycatalog2morton)
lat_max = max(lat_mycatalog2morton)

# Make lists for plotting the 1:1 line
x_lat = np.linspace(lat_min, lat_max, 10)
y_lat = np.linspace(lat_min, lat_max, 10)
plt.scatter(lat_mycatalog2morton,lat_morton2mycatalog, s=15)
plt.plot(x_lat,y_lat, 'k--')
plt.xlabel('Latitudes of Our Catalog ($^\circ$)')
plt.ylabel('Latitudes of Morton et al. (2023) ($^\circ$)')
plt.title('Latitudes of Our Catalog vs.Latitudes of Morton et al. (2023)')

### Compare with the ANSS Catalog 

In [ ]:
# Plot the scatter plot
plt.figure()
lat_min = min(lat_mycatalog2anss)
lat_max = max(lat_mycatalog2anss)

# Make lists for plotting the 1:1 line
x_lat = np.linspace(lat_min, lat_max, 10)
y_lat = np.linspace(lat_min, lat_max, 10)
plt.scatter(lat_mycatalog2anss,lat_anss2mycatalog, s=15)
plt.plot(x_lat,y_lat, 'k--')
plt.xlabel('Latitudes of Our Catalog ($^\circ$)')
plt.ylabel('Latitudes of ANSS Catalog ($^\circ$)')
plt.title('Latitudes of Our Catalog vs. ANSS Catalog')

## Plot the Longitudes

### Compare with Morton's Catalog 

In [ ]:
# Plot the scatter plot
plt.figure()
lon_min = min(lon_mycatalog2morton)
lon_max = max(lon_mycatalog2morton)

# Make lists for plotting the 1:1 line
x_lon = np.linspace(lon_min, lon_max, 10)
y_lon = np.linspace(lon_min, lon_max, 10)
plt.scatter(lon_mycatalog2morton,lon_morton2mycatalog)
plt.plot(x_lon,y_lon, 'k--')
plt.xlabel('Longitudes of Our Catalog ($^\circ$)')
plt.ylabel('Longitudes of Morton et al. (2023) ($^\circ$)')
plt.title('Longitudes of Our Catalog vs.Latitudes of Morton et al. (2023)')

### Compare with the ANSS Catalog 

In [ ]:
# Plot the scatter plot
plt.figure()
lon_min = min(lon_mycatalog2anss)
lon_max = max(lon_mycatalog2anss)

# Make lists for plotting the 1:1 line
x_lon = np.linspace(lon_min, lon_max, 10)
y_lon = np.linspace(lon_min, lon_max, 10)
plt.scatter(lon_mycatalog2anss,lon_anss2mycatalog)
plt.plot(x_lon,y_lon, 'k--')
plt.xlabel('Longitudes of Our Catalog ($^\circ$)')
plt.ylabel('Longitudes of Morton et al. (2023) ($^\circ$)')
plt.title('Longitudes of Our Catalog vs.Latitudes of Morton et al. (2023)')

## Histograms
Make histograms of mycatalog vs. Morton's catalog

### Histogram: All of our catalog 

In [ ]:
events = pd.read_csv('../../data/datasets_all_years/events_pnsn_wa.csv')

In [ ]:
# Plot the same histogram but overlay the histograms
bins = np.linspace(5,30,25)

plt.hist(unmatched_events_mycatalog2morton_and_anss['picks'], bins=bins,  
         alpha=0.5, # the transaparency parameter 
         label='Newly detected events') 
plt.hist(matched_events_mycatalog2anss['picks'], bins=bins,
         alpha=0.5, 
         label='Events matching the ANSS Catalog')   
plt.hist(matched_events_mycatalog2morton['picks'], bins=bins,
         alpha=0.5, 
         label='Events matching Morton et al., 2023') 

plt.xlabel('Number of Picks')
plt.ylabel('Number of Events')  
plt.legend(loc='upper right') 
plt.title('Picks vs. Number of Events') 
plt.show()


### Histogram: Matched events alone

### Compare with Morton et al. (2023)

In [ ]:
# Plot the histogram of the number of picks for the matched events
plt.figure()
bins = np.linspace(5,30,25)
plt.hist(matched_events_mycatalog2morton['picks'],bins=bins)
plt.xlabel('Number of Picks')
plt.ylabel('Number of Events')
plt.title('Histogram of Matched Events with Morton et al. (2023): Picks vs. the Number of Events')

### Compare with ANSS 

In [ ]:
# Plot the histogram of the number of picks for the matched events
plt.figure()
bins = np.linspace(5,30,25)
plt.hist(matched_events_mycatalog2anss['picks'],bins=bins)
plt.xlabel('Number of Picks')
plt.ylabel('Number of Events')
plt.title('Histogram of Matched Events with ANSS: Picks vs. the Number of Events')

## 2. Filter events 
Filter Events based on the following criteria
1. For an event, at least two stations have to be less than 50 km from the event and no station can be 100 km apart from each other.
2. An event has to have more than or equal to 6 picks


In [9]:
# Read the new events file
year= 'pnsn_jdf'
events = pd.read_csv(f'../data/datasets_{year}/new_events.csv')
events

Unnamed: 0.1  Unnamed: 0    idx                              time  \
0                 0           0      1  2011-12-10 22:44:45.831192+00:00   
1                 1           6      2  2011-12-26 18:06:14.336595+00:00   
2                 2          46     24  2012-06-12 23:24:49.168208+00:00   
3                 3          65     29  2012-09-01 03:49:53.850651+00:00   
4                 4          71     30  2012-09-01 04:51:30.154350+00:00   
...             ...         ...    ...                               ...   
16973         16973      175244  31055  2015-09-13 13:14:34.524904+00:00   
16974         16974      175263  31062  2015-09-14 05:33:02.400734+00:00   
16975         16975      175271  31063  2015-09-14 06:09:08.330498+00:00   
16976         16976      175281  31064  2015-09-14 13:34:01.190085+00:00   
16977         16977      175290  31068  2015-09-15 09:12:53.198694+00:00   

                x           y          z  picks   latitude   longitude  \
0      -96.868991   57.435553  12.890625      6  45.010235 -126.728790   
1       -8.037165  129.232778   0.390625      7  45.662816 -125.603130   
2      -10.575217  555.229645  49.609375      6  49.494294 -125.645976   
3     -181.470729 -367.364693   4.296875      6  41.172777 -127.662482   
4     -103.637130 -405.656546   0.390625      7  40.841734 -126.728844   
...           ...         ...        ...    ...        ...         ...   
16973 -171.318521 -397.280203  47.265625      6  40.905779 -127.533275   
16974  -57.952191 -367.364693   0.390625      8  41.191011 -126.190794   
16975 -145.091982 -447.538261  49.609375     10  40.458469 -127.210546   
16976 -161.166312 -434.375436  49.609375      9  40.573981 -127.403307   
16977 -148.476051 -277.618162   1.171875      6  41.987149 -127.291699   

           depth  event_idx  pick_idx  residual station phase     time_pick  \
0      12.890625          1   1655834  0.594705    J35A     P  1.323557e+09   
1       0.390625          2   1654163 -0.086003    J35A     P  1.324923e+09   
2      49.609375         24    207246 -0.292191    J43A     P  1.339544e+09   
3       4.296875         29    309907 -0.235134    G11B     P  1.346471e+09   
4       0.390625         30    169329 -0.749538    G03B     P  1.346475e+09   
...          ...        ...       ...       ...     ...   ...           ...   
16973  47.265625      31055   1511593 -0.463433    G10D     P  1.442150e+09   
16974   0.390625      31062   1476568 -0.072230    G10D     P  1.442209e+09   
16975  49.609375      31063   1476574 -0.554440    G10D     P  1.442211e+09   
16976  49.609375      31064   1476584  0.269303    G10D     P  1.442238e+09   
16977   1.171875      31068   1452051  0.333196    G10D     P  1.442308e+09   

                               datetime  
0      2011-12-10 22:44:45.831192+00:00  
1      2011-12-26 18:06:14.336595+00:00  
2      2012-06-12 23:24:49.168208+00:00  
3      2012-09-01 03:49:53.850651+00:00  
4      2012-09-01 04:51:30.154350+00:00  
...                                 ...  
16973  2015-09-13 13:14:34.524904+00:00  
16974  2015-09-14 05:33:02.400734+00:00  
16975  2015-09-14 06:09:08.330498+00:00  
16976  2015-09-14 13:34:01.190085+00:00  
16977  2015-09-15 09:12:53.198694+00:00  

[16978 rows x 18 columns]

In [10]:
all_pick_assignments = pd.read_csv(f'../data/datasets_{year}/all_pick_assignments_{year}.csv')
mycatalog = all_pick_assignments.drop_duplicates(subset=['idx'])
mycatalog

Unnamed: 0    idx                              time           x  \
0                0      1  2011-12-10 22:44:45.831192+00:00  -96.868991   
6                6      2  2011-12-26 18:06:14.336595+00:00   -8.037165   
13              13      7  2012-02-04 20:05:31.203164+00:00 -200.083112   
20              20      8  2012-02-06 08:17:12.359449+00:00  -67.258382   
26              26     11  2012-02-16 06:37:34.356357+00:00   68.950417   
...            ...    ...                               ...         ...   
175263      175263  31062  2015-09-14 05:33:02.400734+00:00  -57.952191   
175271      175271  31063  2015-09-14 06:09:08.330498+00:00 -145.091982   
175281      175281  31064  2015-09-14 13:34:01.190085+00:00 -161.166312   
175290      175290  31068  2015-09-15 09:12:53.198694+00:00 -148.476051   
175296      175296  31069  2015-09-15 17:31:03.343072+00:00   68.950417   

                 y          z  picks   latitude   longitude      depth  \
0        57.435553  12.890625      6  45.010235 -126.728790  12.890625   
6       129.232778   0.390625      7  45.662816 -125.603130   0.390625   
13      484.629041  49.609375      7  48.827345 -128.225159  49.609375   
20     -124.450749   3.515625      6  43.376931 -126.329931   3.515625   
26      488.218902  49.609375      6  48.888012 -124.559792  49.609375   
...            ...        ...    ...        ...         ...        ...   
175263 -367.364693   0.390625      8  41.191011 -126.190794   0.390625   
175271 -447.538261  49.609375     10  40.458469 -127.210546  49.609375   
175281 -434.375436  49.609375      9  40.573981 -127.403307  49.609375   
175290 -277.618162   1.171875      6  41.987149 -127.291699   1.171875   
175296 -466.684187  49.609375      6  40.295865 -124.689054  49.609375   

        event_idx  pick_idx  residual station phase     time_pick  
0               1   1655834  0.594705    J35A     P  1.323557e+09  
6               2   1654163 -0.086003    J35A     P  1.324923e+09  
13              7    345847 -1.237492    J35A     P  1.328386e+09  
20              8    121103 -0.180289    J35A     P  1.328516e+09  
26             11     87298 -0.443887    J35A     P  1.329374e+09  
...           ...       ...       ...     ...   ...           ...  
175263      31062   1476568 -0.072230    G10D     P  1.442209e+09  
175271      31063   1476574 -0.554440    G10D     P  1.442211e+09  
175281      31064   1476584  0.269303    G10D     P  1.442238e+09  
175290      31068   1452051  0.333196    G10D     P  1.442308e+09  
175296      31069   1452085  0.041425    G10D     P  1.442338e+09  

[19036 rows x 16 columns]

In [18]:
count = 0

In [11]:
"""
Inputs:
1. Either of the following files can be the input:
    1. matched_events_with_morton_mycatalog.csv from the 4_quality_control file
    2. matched_events_with_anss_mycatalog.csv from the 4_quality_control file
    3. new_events.csv from the 4_quality_control file
2. The all_pick_assignments CSV file from the 3_associate file: e.g., all_pick_assignments = pd.read_csv('../data/datasets_2012/all_pick_assignments_2012.csv')


Outputs:
1. A new dataframe that only has events that fall into the following categories:
    1. For an event, at least two stations have to be less than 50 km from the event and no station can be 100 km apart from each other.
2. An event has to have more than or equal to 6 picks
"""

# Parameters
client2 = Client("IRIS")

mycatalog = all_pick_assignments.drop_duplicates(subset=['idx'])
mycatalog['datetime'] = pd.to_datetime(mycatalog['time'], utc = True)

for i, idx in tqdm(enumerate(events['idx']),total=len(events['idx'])):
    event = mycatalog
    picks = all_pick_assignments
    picks_idx = picks.loc[picks['idx']==idx]
    pick_sta = np.unique(picks_idx['station'])
    otime = UTCDateTime(str(event[event['idx'] == idx]["datetime"].values[0]))
    distances = []
    max_dist = 10
    min_dist = 0
    for station in pick_sta:


        sta_inv = client2.get_stations(network='*',
                                       station=station, channel="?H?", 
                                       starttime=otime - 1e8, endtime=otime + 1e8,level="response")
        if len(sta_inv) == 0:
            print(f"Failed to fetch for {networks} {station} {otime}")
            continue

        _network = sta_inv[0].code
        slat = sta_inv[0][0].latitude
        slon = sta_inv[0][0].longitude
        olat = event.loc[event['idx']==idx, 'latitude'].values[0]
        olon = event.loc[event['idx']==idx, 'longitude'].values[0]

        dis1 = locations2degrees(olat, olon, slat, slon)
        dist = degrees2kilometers(dis1)

        distances.append([None, _network, station, dist])

    # Sort distances
    distances = sorted(distances, key=lambda item: item[-1])

    # This is for the first criterion in the markdown above
    # Determine if any two of the numbers in the distances list are less than or equal to 50
    found = False
    for i in range(len(distances)):
        for j in range(i + 1, len(distances)):
            if distances[i][3] <= 50 and distances[j][3] <= 50:
                found = True
                break
        if found:
            break

    # Make a list that includes the differences between the consecutive numbers in the distances list.
    differences = [distances[i+1][3] - distances[i][3] for i in range(len(distances) - 1)]

    if found == False: # If there were not at least two distances between the station and the event less than or equal to 50 km
        print(distances)
        index = events[events['idx'] == idx].index
        events = events.drop(index=index)

    elif any(differences > 100 for differences in differences): # If any of the distances between two stations were greater than 100 km
        print(distances)
        index = events[events['idx'] == idx].index
        events = events.drop(index=index)

    else: 
        continue


events 

/tmp/ipykernel_1409532/2718798803.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  mycatalog['datetime'] = pd.to_datetime(mycatalog['time'], utc = True)
  0%|          | 1/16978 [00:00<3:40:58,  1.28it/s]

[[None, '7D', 'J35A', 65.27066560804593], [None, '7D', 'J43A', 132.65455166267267], [None, '7D', 'J51A', 203.42561430408975], [None, '7D', 'J59A', 278.9593012725096]]


  0%|          | 2/16978 [00:01<4:04:09,  1.16it/s]

[[None, '7D', 'J35A', 54.7718435526121], [None, '7D', 'J43A', 68.75940916889705], [None, '7D', 'J51A', 133.29236020809185], [None, '7D', 'J59A', 214.52429090037188]]


  0%|          | 3/16978 [00:02<3:40:52,  1.28it/s]

...

100%|█████████▉| 16977/16978 [3:32:40<00:00,  1.60it/s]

[[None, 'Z5', 'GB331', 69.56117616995456], [None, 'Z5', 'GB281', 121.55126449185003], [None, '7D', 'G10D', 157.7239127791814], [None, 'Z5', 'GB101', 174.66988649772532], [None, '7D', 'G26D', 234.98295642856786]]


100%|██████████| 16978/16978 [3:32:40<00:00,  1.33it/s]

[[None, 'Z5', 'GB101', 58.26411628985903], [None, 'Z5', 'GB281', 146.2161462276387], [None, '7D', 'G26D', 163.93053610412827], [None, '7D', 'G10D', 196.87019125122137]]


Unnamed: 0.1  Unnamed: 0    idx                              time  \
11               11         138     45  2012-09-03 21:04:23.801686+00:00   
13               13         156     47  2012-09-04 01:39:12.775704+00:00   
14               14         167     48  2012-09-04 05:14:32.693892+00:00   
19               19         246     63  2012-09-05 02:21:21.324186+00:00   
23               23         318     73  2012-09-05 20:02:27.396777+00:00   
...             ...         ...    ...                               ...   
16937         16937      174908  30990  2015-09-07 11:42:49.936779+00:00   
16945         16945      174984  31004  2015-09-08 16:45:36.819927+00:00   
16969         16969      175204  31047  2015-09-12 15:11:46.290080+00:00   
16971         16971      175218  31052  2015-09-13 02:25:30.014925+00:00   
16974         16974      175263  31062  2015-09-14 05:33:02.400734+00:00   

               x           y          z  picks   latitude   longitude  \
11     79.102626 -460.701085  27.734375     12  40.348842 -124.568925   
13     60.490243 -429.588955  44.921875     11  40.630554 -124.785015   
14      3.807078 -452.324742  27.734375      6  40.428014 -125.455136   
19     61.336260 -455.914604  31.640625     10  40.393438 -124.777565   
23    -65.566347 -330.269460   0.390625      8  41.524408 -126.285554   
...          ...         ...        ...    ...        ...         ...   
16937   0.423009 -374.544416   0.390625      7  41.128434 -125.494962   
16945 -24.957513 -361.381591  37.890625      6  41.246571 -125.797748   
16969 -13.113269 -366.168073   0.390625      8  41.203751 -125.656342   
16971 -63.028295 -391.297101   0.390625      7  40.975151 -126.248847   
16974 -57.952191 -367.364693   0.390625      8  41.191011 -126.190794   

           depth  event_idx  pick_idx  residual station phase     time_pick  \
11     27.734375         45    137798 -0.779532   FS01B     P  1.346706e+09   
13     44.921875         47     84891 -0.525267   FS01B     P  1.346723e+09   
14     27.734375         48   1723453 -0.350261   FS01B     S  1.346736e+09   
19     31.640625         63     12601 -1.192150   FS01B     P  1.346812e+09   
23      0.390625         73   1763444  0.503721    G02B     S  1.346875e+09   
...          ...        ...       ...       ...     ...   ...           ...   
16937   0.390625      30990   1639962 -1.224569    G10D     P  1.441626e+09   
16945  37.890625      31004   1315524 -0.614043    G10D     P  1.441731e+09   
16969   0.390625      31047   1318025 -0.366062    G10D     P  1.442071e+09   
16971   0.390625      31052   2817933 -0.108673    G10D     S  1.442111e+09   
16974   0.390625      31062   1476568 -0.072230    G10D     P  1.442209e+09   

                               datetime  
11     2012-09-03 21:04:23.801686+00:00  
13     2012-09-04 01:39:12.775704+00:00  
14     2012-09-04 05:14:32.693892+00:00  
19     2012-09-05 02:21:21.324186+00:00  
23     2012-09-05 20:02:27.396777+00:00  
...                                 ...  
16937  2015-09-07 11:42:49.936779+00:00  
16945  2015-09-08 16:45:36.819927+00:00  
16969  2015-09-12 15:11:46.290080+00:00  
16971  2015-09-13 02:25:30.014925+00:00  
16974  2015-09-14 05:33:02.400734+00:00  

[4520 rows x 18 columns]

In [ ]:
new_events_filtered = filter_sta(new_events, mycatalog_picks)

In [ ]:
new_events_filtered.to_csv(f'../data/datasets_{year}/new_events_filtered_pnsn_wa.csv')

In [12]:
events.to_csv(f'../data/datasets_{year}/new_events_filtered_pnsn_jdf.csv')

In [26]:
events

Unnamed: 0.1  Unnamed: 0     idx                              time  \
2                 2          22       9  2011-01-01 21:15:59.281683+00:00   
13               13         160      34  2011-01-03 07:33:08.560877+00:00   
15               15         207      39  2011-01-03 08:33:59.698375+00:00   
17               17         220      41  2011-01-03 09:42:18.324354+00:00   
19               19         239      43  2011-01-03 11:03:16.972894+00:00   
...             ...         ...     ...                               ...   
77999         77999      734115  196379  2015-12-30 01:54:02.995317+00:00   
78009         78009      734272  196395  2015-12-31 08:12:36.917788+00:00   
78010         78010      734278  196396  2015-12-31 09:42:08.772727+00:00   
78011         78011      734285  196397  2015-12-31 14:01:51.097809+00:00   
78013         78013      734299  196400  2015-12-31 16:08:33.417892+00:00   

                x           y          z  picks   latitude   longitude  \
2      178.932677  466.679734   8.984375      7  48.672531 -123.070417   
13     116.327390 -422.409232  47.265625     10  40.689219 -124.123839   
15     119.711460 -392.493722  31.640625      7  40.958039 -124.078076   
17     141.707912 -459.504465  49.609375     10  40.351336 -123.831996   
19     192.468955  460.696632   0.390625     13  48.614762 -122.889588   
...           ...         ...        ...    ...        ...         ...   
77999   79.102626 -427.195714  33.203125      6  40.650531 -124.564744   
78009   83.332712 -430.785575   1.171875      6  40.617793 -124.515212   
78010  195.007007 -452.324742   4.296875      7  40.405197 -123.202845   
78011  185.700816 -467.880808  48.046875      7  40.267332 -123.316911   
78013   86.716782 -430.785575  18.359375      6  40.617445 -124.475227   

           depth  event_idx  pick_idx  residual station phase     time_pick  \
2       8.984375          9  17476232  1.021405    LRIV     S  1.293917e+09   
13     47.265625         34   9298994  0.108464     JCC     P  1.294040e+09   
15     31.640625         39   9298998  0.002486     JCC     P  1.294044e+09   
17     49.609375         41   9299000 -0.187211     JCC     P  1.294048e+09   
19      0.390625         43   9900576  0.831680    LRIV     P  1.294053e+09   
...          ...        ...       ...       ...     ...   ...           ...   
77999  33.203125     196379   8780969 -0.090423     JCC     P  1.451440e+09   
78009   1.171875     196395   8066503  0.018756     JCC     P  1.451550e+09   
78010   4.296875     196396   8066506  0.429082     JCC     P  1.451555e+09   
78011  48.046875     196397   8066510  0.177298     JCC     P  1.451571e+09   
78013  18.359375     196400   8066517  0.016042     JCC     P  1.451578e+09   

                               datetime  
2      2011-01-01 21:15:59.281683+00:00  
13     2011-01-03 07:33:08.560877+00:00  
15     2011-01-03 08:33:59.698375+00:00  
17     2011-01-03 09:42:18.324354+00:00  
19     2011-01-03 11:03:16.972894+00:00  
...                                 ...  
77999  2015-12-30 01:54:02.995317+00:00  
78009  2015-12-31 08:12:36.917788+00:00  
78010  2015-12-31 09:42:08.772727+00:00  
78011  2015-12-31 14:01:51.097809+00:00  
78013  2015-12-31 16:08:33.417892+00:00  

[26691 rows x 18 columns]

In [ ]:
count = 0
for i, idx in enumerate(range(0,10,1)):
    print(i,idx,count)
    count+=1

print(count)

In [ ]:
new_events

## Plot using the plotting functions

In [ ]:
all_picks = pd.read_csv('../data/datasets_2014/all_picks_2014_for_assoc.csv')

In [ ]:
all_picks

In [ ]:
all_picks_networks = all_picks['station_network_code'].drop_duplicates()
list_networks = list(all_picks_networks)
all_picks_networks = ','.join(all_picks_networks)
all_picks_networks

In [ ]:
list_networks

In [ ]:
# Clean up the memory
del all_picks

## Plot the offshore events north of 44&deg; N

In [ ]:
new_events = pd.read_csv('../data/datasets_2014/new_events.csv')

In [ ]:
new_events_44N_and_above= new_events.loc[(new_events['latitude']>44)&(new_events['longitude']<-124)]
new_events_44N_and_above = new_events_44N_and_above[0:50] 

In [ ]:
# parameters for subplots_cluster_scale
mycatalog= mycatalog
mycatalog_picks=mycatalog_picks
networks= all_picks_networks
channel= "?H?"
idx_sta= 50
title= "Events matched"
fig_title= "new_events_filtered_44N_and_above_plots.pdf"

subplots_cluster_scale(new_events_44N_and_above,mycatalog_picks,networks,channel,idx_sta,title,fig_title)

## Plot one of the cluster events at around 46.5&deg; N, 125&deg; W using the plotting functions 

In [ ]:
def subplots_cluster_scale_p(idx, mycatalog, mycatalog_picks, networks, channel, idx_sta, title, fig_title):
    """
    idx: event_idx
    mycatalog: dataframe that contains only the unique picks (i.e., mycatalog_picks.drop_duplicates(subset=['idx']).copy())
    mycatalog_picks: all pick assignments csv file (e.g., pd.read_csv('../data/datasets_OR/all_pick_assignments_OR.csv'))
    networks: string of networks (e.g., "NV,OO,7A")
    channel: specify the direction of the channel (i.e., "?HZ", "?HE" or "?HN")
    idx_sta: choose the station to which you want to show the waveforms
    title: title in a string
    fig_title: figure title in as string
    """
        
    # Define the clients 
    client_waveform = WaveformClient()
    client2 = Client("IRIS")
    client_ncedc = Client('NCEDC')


    # Plot the earthquake moveout for one of the unmatched events for all stations 
    event = mycatalog
    picks = mycatalog_picks
    picks_idx = picks.loc[picks['idx']==idx]
    pick_sta = np.unique(picks_idx['station'])
    
    otime = UTCDateTime(str(event[event['idx'] == idx]["datetime"].values[0]))
    distances = []
    max_dist = 10
    min_dist = 0
    
    print(event[event['idx'] == idx]['picks'].values[0])
    for station in pick_sta:
        
        
        sta_inv = client2.get_stations(network=networks,
                                       station=station, channel="?H?", 
                                       starttime=otime - 1e8, endtime=otime + 1e8,level="response")
        if len(sta_inv) == 0:
#             print(f"Failed to fetch for {networks} {station} {otime}")
            continue
            
        _network = sta_inv[0].code
        slat = sta_inv[0][0].latitude
        slon = sta_inv[0][0].longitude
        olat = event.loc[event['idx']==idx, 'latitude'].values[0]
        olon = event.loc[event['idx']==idx, 'longitude'].values[0]
        
        dis1 = locations2degrees(olat, olon, slat, slon)
        dist = degrees2kilometers(dis1)
#         if max_dist < dist:
#             max_dist = dist
            
#         if min_dist > dist:
#             min_dist = dist
            
        distances.append([None, _network, station, dist])

    # Sort distances
    distances = sorted(distances, key=lambda item: item[-1])
    distances = distances[:idx_sta+1]
    
    # Set up to define the xlim and ylim
    max_y = 0
    min_y = 0
    # This count is for the if statements. Only used to ensure that min_y_count 
    #is changed from 0 to either the first positive value of the distance of one of the stations from the event
    min_y_count = 0 
    
    max_x = 0
    min_x = 0
    
    # This count is for the if statements. Only used to ensure that min_x_count 
    #is changed from 0 to either the first positive value of P pick time or the first positive value of S pick time
    min_x_count= 0
    # Create a figure
    fig,axs = plt.subplots(1,4,figsize=(18,6))
    gs = fig.add_gridspec(3, hspace=0, figure=fig)
#     axs = gs.subplots(sharex=True, sharey=True)
    starttime = otime -30
    endtime = otime + 120
    
    # Define texts
    texts = []
    
    for i, ii in enumerate(distances):
            
        if ii[1] in ['NC', 'BK']:
            # Query waveforms
            st = client_ncedc.get_waveforms(network=ii[1], station=ii[2], location="*", channel=channel,starttime=starttime, endtime=endtime)

        elif ii[1] in networks: 
            st = client_waveform.get_waveforms(network=ii[1], station=ii[2], channel=channel,starttime=starttime, endtime=endtime)
  
        else: 
            st =  Stream()
            print(f"WARNING: No data for {ii[1]}.{ii[2]}.{channel} on {otime}.")    
            continue
            
#         print(f"len(st):{len(st)}")
#         print(st)
    
        # Skip empty traces
        if len(st) == 0:
                continue
                
        sta_picks = picks_idx[picks_idx['station'] == ii[2]]
        p_picks = sta_picks.loc[sta_picks['phase'] == 'P']
        s_picks = sta_picks.loc[sta_picks['phase'] == 'S']
#         print(len(p_picks),len(s_picks))
        
        # Define the xlim values
        # Define the maximum x value
        if len(s_picks) > 0:
            if max_x < UTCDateTime(s_picks.iloc[0]['time_pick']) - starttime:
                max_x = UTCDateTime(s_picks.iloc[0]['time_pick']+5) - starttime
        elif len(p_picks) > 0:
            if max_x < UTCDateTime(p_picks.iloc[0]['time_pick']) - starttime: 
                max_x = UTCDateTime(p_picks.iloc[0]['time_pick']+5) - starttime
        else:
            print('No picks for this station. Skipping.')
            continue 
            
        # Define the minimum x value
        if len(p_picks) > 0:
            if min_x_count == 0:
                if min_x < UTCDateTime(p_picks.iloc[0]['time_pick']) - starttime:
                    min_x = UTCDateTime(p_picks.iloc[0]['time_pick']-5) - starttime
                    min_x_count += 1           
            else:
                if min_x >= UTCDateTime(p_picks.iloc[0]['time_pick']) - starttime:
                    min_x = UTCDateTime(p_picks.iloc[0]['time_pick']-5) - starttime            
        elif len(s_picks) > 0:
            if min_x_count == 0:
                if min_x < UTCDateTime(s_picks.iloc[0]['time_pick'])- starttime:
                    min_x = UTCDateTime(s_picks.iloc[0]['time_pick']-5)- starttime
                    min_x_count += 1                
            else:
                if min_x >= UTCDateTime(s_picks.iloc[0]['time_pick'])- starttime:
                    min_x = UTCDateTime(s_picks.iloc[0]['time_pick']-5) - starttime
        else:
            print('No picks for this station. Skipping.')
            continue    
            
        if len(p_picks) == 0:
            continue
            
#         print('This is after the p_pick continue statement')
    
        # Define ylim values
        if min_y_count == 0:
            if min_y < ii[3]:
                min_y = ii[3] - 5
                min_y_count += 1           
        else:
            if min_y >= ii[3]:
                min_y = ii[3] - 5 
                
        max_y = ii[3] + 5
        
    scaling_factor = (1/2)*(max_y-min_y)   
        
    for i, ii in enumerate(distances):
            
        if ii[1] in ['NC', 'BK']:
            # Query waveforms
            st = client_ncedc.get_waveforms(network=ii[1], station=ii[2], location="*", channel=channel,starttime=starttime, endtime=endtime)

        elif ii[1] in networks: 
            st = client_waveform.get_waveforms(network=ii[1], station=ii[2], channel=channel,starttime=starttime, endtime=endtime)
  
        else: 
            st =  Stream()
            print(f"WARNING: No data for {ii[1]}.{ii[2]}.{channel} on {otime}.")    
            continue
            
#         print(f"len(st):{len(st)}")
#         print(st)
    
        # Skip empty traces
        if len(st) == 0:
                continue
        _st = Stream()
        # Check for HH and BH channels presence
        has_HH = bool(st.select(channel="HH?"))
        has_BH = bool(st.select(channel="BH?"))

        # Apply selection logic based on channel presence
        if has_HH and has_BH:
            # If both HH and BH channels are present, select only HH
            _st += st.select(channel="HH?")
        elif has_HH:
            # If only HH channels are present
            _st += st.select(channel="HH?")
        elif has_BH:
            # If only BH channels are present
            _st += st.select(channel="BH?")

        st = _st

        print(f'Second st print:{_st}')
              
        st = Stream(filter(lambda st: st.stats.sampling_rate > 10, st))
        st.taper(max_percentage=0.05)
        st.filter(type='bandpass', freqmin=2, freqmax=25)
        st.merge(fill_value='interpolate') # fill gaps if there are any.

#         print(st)
        # Select only one trace per channel
        unique_channels = set(tr.stats.channel for tr in st)
        selected_traces = []
        
        for ch in unique_channels:
            selected_traces.append(next(tr for tr in st if tr.stats.channel == ch))
        st = Stream(selected_traces)
                   
        trim_st = st.copy()
        sta_picks = picks_idx[picks_idx['station'] == ii[2]]
        p_picks = sta_picks.loc[sta_picks['phase'] == 'P']
        s_picks = sta_picks.loc[sta_picks['phase'] == 'S']
#         print(len(p_picks),len(s_picks))
        
        
                
            
        if len(p_picks) == 0:
            continue 
#         print('This is after the p_pick continue statement')
        print(trim_st)
        
        for iax in range(len(trim_st)):
            print(iax)
            sampling_rate = trim_st[iax].stats.sampling_rate
            trim_st = trim_st.normalize()
            
            tp = UTCDateTime(p_picks.iloc[0]['time_pick']) - otime + 30
            i1 = int((tp-5)*sampling_rate)
            i2 = int((tp+15)*sampling_rate)

            offsets1 = ii[3]
            try: 
                wave = trim_st[iax].data
                wave = wave / (np.nanmax(wave[i1:i2], axis=-1)*10)
            except:
                continue 
            
#             print(trim_st[iax].stats.sampling_rate)
            axs[iax].plot(trim_st[iax].times(), wave * scaling_factor + offsets1, 
                          color='black', label=f"{trim_st[iax].stats.channel}", alpha=0.7, lw=0.5)
#             axs[iax].plot(trim_st[iax].times(), wave * 30 + offsets1, color='black', label=f"{trim_st[iax].stats.channel}", alpha=0.7, lw=0.5)

#             axs[iax].text(xlim[-1] + 2,   offsets1, 
#                               [ii[2]], fontsize=8, verticalalignment='bottom')

            if len(p_picks) > 0:
                axs[iax].vlines(UTCDateTime(p_picks.iloc[0]['time_pick']) - otime + 30, offsets1 - (1/35) * scaling_factor, 
                                offsets1 + (1/35) * scaling_factor, color='r')
            if len(s_picks) > 0:
                axs[iax].vlines(UTCDateTime(s_picks.iloc[0]['time_pick']) - otime + 30, offsets1 - (1/35) * scaling_factor, 
                                offsets1 + (1/35) * scaling_factor, color='b')
        texts.append([ii[2],ii[3]])

    
#     print(max_y,min_y)
    chs = ['2','1','Z']
    for iax in range(3):
        for i, ii in enumerate(texts):
            offsets1 = ii[1]
            axs[iax].text(max_x + 0.5, offsets1, 
                                  [ii[0]], fontsize=8, verticalalignment='bottom')
        axs[iax].legend(chs[iax],loc='upper right', handlelength=0)
        axs[iax].set_ylim([min_y,max_y])
        axs[iax].set_xlim([min_x,max_x])
        axs[iax].grid(alpha=0.5)
    fig.supxlabel('Time [sec]', y=0.07)
    fig.supylabel('Distance [km]')
    fig.suptitle(f"{title}: Origin Time={otime}, \n Latitude={round(event[event['idx']==idx]['latitude'].values[0], 2)}, Longtitude={round(event[event['idx']==idx]['longitude'].values[0], 2)}, Depth={round(event[event['idx']==idx]['depth'].values[0], 2)}", y=1)
    
    m = Basemap(projection='merc', llcrnrlat=40, urcrnrlat=50, llcrnrlon=-130, urcrnrlon=-120, resolution='i', ax=axs[3])
    m.drawcoastlines()
    m.drawcountries()
    m.drawstates()
    m.drawmapboundary()
    m.drawparallels(np.arange(40, 51, 1), labels=[1,0,0,0])
    m.drawmeridians(np.arange(-130, -119, 1), labels=[0,0,0,1])
    x, y = m(event[event['idx']==idx]['longitude'].values[0], event[event['idx']==idx]['latitude'].values[0])
    m.plot(x, y, 'ro', markersize=9)
    axs[3].set_title('Event Location')
    
    plt.show()


In [ ]:
def subplots_cluster_scale(idx, mycatalog, mycatalog_picks, networks, channel, idx_sta, title, fig_title):
    """
    idx: event_idx
    mycatalog: dataframe that contains only the unique picks (i.e., mycatalog_picks.drop_duplicates(subset=['idx']).copy())
    mycatalog_picks: all pick assignments csv file (e.g., pd.read_csv('../data/datasets_OR/all_pick_assignments_OR.csv'))
    networks: string of networks (e.g., "NV,OO,7A")
    channel: specify the direction of the channel (i.e., "?HZ", "?HE" or "?HN")
    idx_sta: choose the station to which you want to show the waveforms
    title: title in a string
    fig_title: figure title in as string
    """
        
    # Define the clients 
    client_waveform = WaveformClient()
    client2 = Client("IRIS")
    client_ncedc = Client('NCEDC')


    # Plot the earthquake moveout for one of the unmatched events for all stations 
    event = mycatalog
    picks = mycatalog_picks
    
    p = PdfPages(fig_title) 
    
    for idx in event['idx']:
        
        picks_idx = picks.loc[picks['idx']==idx]
        pick_sta = np.unique(picks_idx['station'])

        otime = UTCDateTime(str(event[event['idx'] == idx]["datetime"].values[0]))
        distances = []
        max_dist = 10
        min_dist = 0

        print(event[event['idx'] == idx]['picks'].values[0])
        for station in pick_sta:


            sta_inv = client2.get_stations(network=networks,
                                           station=station, channel="?H?", 
                                           starttime=otime - 1e8, endtime=otime + 1e8,level="response")
            if len(sta_inv) == 0:
    #             print(f"Failed to fetch for {networks} {station} {otime}")
                continue

            _network = sta_inv[0].code
            slat = sta_inv[0][0].latitude
            slon = sta_inv[0][0].longitude
            olat = event.loc[event['idx']==idx, 'latitude'].values[0]
            olon = event.loc[event['idx']==idx, 'longitude'].values[0]

            dis1 = locations2degrees(olat, olon, slat, slon)
            dist = degrees2kilometers(dis1)
    #         if max_dist < dist:
    #             max_dist = dist

    #         if min_dist > dist:
    #             min_dist = dist

            distances.append([None, _network, station, dist])

        # Sort distances
        distances = sorted(distances, key=lambda item: item[-1])
        distances = distances[:idx_sta+1]

        # Set up to define the xlim and ylim
        max_y = 0
        min_y = 0
        # This count is for the if statements. Only used to ensure that min_y_count 
        #is changed from 0 to either the first positive value of the distance of one of the stations from the event
        min_y_count = 0 

        max_x = 0
        min_x = 0

        # This count is for the if statements. Only used to ensure that min_x_count 
        #is changed from 0 to either the first positive value of P pick time or the first positive value of S pick time
        min_x_count= 0
        # Create a figure
        fig,axs = plt.subplots(1,4,figsize=(18,6))
        gs = fig.add_gridspec(3, hspace=0, figure=fig)
    #     axs = gs.subplots(sharex=True, sharey=True)
        starttime = otime -30
        endtime = otime + 120

        # Define texts
        texts = []

        for i, ii in enumerate(distances):

            if ii[1] in ['NC', 'BK']:
                # Query waveforms
                st = client_ncedc.get_waveforms(network=ii[1], station=ii[2], location="*", channel=channel,starttime=starttime, endtime=endtime)

            elif ii[1] in networks: 
                st = client_waveform.get_waveforms(network=ii[1], station=ii[2], channel=channel,starttime=starttime, endtime=endtime)

            else: 
                st =  Stream()
                print(f"WARNING: No data for {ii[1]}.{ii[2]}.{channel} on {otime}.")    
                continue

    #         print(f"len(st):{len(st)}")
    #         print(st)

            # Skip empty traces
            if len(st) == 0:
                    continue

            sta_picks = picks_idx[picks_idx['station'] == ii[2]]
            p_picks = sta_picks.loc[sta_picks['phase'] == 'P']
            s_picks = sta_picks.loc[sta_picks['phase'] == 'S']
    #         print(len(p_picks),len(s_picks))

            # Define the xlim values
            # Define the maximum x value
            if len(s_picks) > 0:
                if max_x < UTCDateTime(s_picks.iloc[0]['time_pick']) - starttime:
                    max_x = UTCDateTime(s_picks.iloc[0]['time_pick']+5) - starttime
            elif len(p_picks) > 0:
                if max_x < UTCDateTime(p_picks.iloc[0]['time_pick']) - starttime: 
                    max_x = UTCDateTime(p_picks.iloc[0]['time_pick']+5) - starttime
            else:
                print('No picks for this station. Skipping.')
                continue 

            # Define the minimum x value
            if len(p_picks) > 0:
                if min_x_count == 0:
                    if min_x < UTCDateTime(p_picks.iloc[0]['time_pick']) - starttime:
                        min_x = UTCDateTime(p_picks.iloc[0]['time_pick']-5) - starttime
                        min_x_count += 1           
                else:
                    if min_x >= UTCDateTime(p_picks.iloc[0]['time_pick']) - starttime:
                        min_x = UTCDateTime(p_picks.iloc[0]['time_pick']-5) - starttime            
            elif len(s_picks) > 0:
                if min_x_count == 0:
                    if min_x < UTCDateTime(s_picks.iloc[0]['time_pick'])- starttime:
                        min_x = UTCDateTime(s_picks.iloc[0]['time_pick']-5)- starttime
                        min_x_count += 1                
                else:
                    if min_x >= UTCDateTime(s_picks.iloc[0]['time_pick'])- starttime:
                        min_x = UTCDateTime(s_picks.iloc[0]['time_pick']-5) - starttime
            else:
                print('No picks for this station. Skipping.')
                continue    

    #         if len(p_picks) == 0:
    #             continue

    #         print('This is after the p_pick continue statement')

            # Define ylim values
            if min_y_count == 0:
                if min_y < ii[3]:
                    min_y = ii[3] - 5
                    min_y_count += 1           
            else:
                if min_y >= ii[3]:
                    min_y = ii[3] - 5 

            max_y = ii[3] + 5

        scaling_factor = (1/2)*(max_y-min_y)   

        for i, ii in enumerate(distances):

            if ii[1] in ['NC', 'BK']:
                # Query waveforms
                st = client_ncedc.get_waveforms(network=ii[1], station=ii[2], location="*", channel=channel,starttime=starttime, endtime=endtime)

            elif ii[1] in networks: 
                st = client_waveform.get_waveforms(network=ii[1], station=ii[2], channel=channel,starttime=starttime, endtime=endtime)

            else: 
                st =  Stream()
                print(f"WARNING: No data for {ii[1]}.{ii[2]}.{channel} on {otime}.")    
                continue

    #         print(f"len(st):{len(st)}")
    #         print(st)

            # Skip empty traces
            if len(st) == 0:
                    continue
            _st = Stream()
            # Check for HH and BH channels presence
            has_HH = bool(st.select(channel="HH?"))
            has_BH = bool(st.select(channel="BH?"))

            # Apply selection logic based on channel presence
            if has_HH and has_BH:
                # If both HH and BH channels are present, select only HH
                _st += st.select(channel="HH?")
            elif has_HH:
                # If only HH channels are present
                _st += st.select(channel="HH?")
            elif has_BH:
                # If only BH channels are present
                _st += st.select(channel="BH?")

            st = _st

            print(f'Second st print:{_st}')

            st = Stream(filter(lambda st: st.stats.sampling_rate > 10, st))
            st.taper(max_percentage=0.05)
            st.filter(type='bandpass', freqmin=2, freqmax=25)
            st.merge(fill_value='interpolate') # fill gaps if there are any.

    #         print(st)
            # Select only one trace per channel
            unique_channels = set(tr.stats.channel for tr in st)
            selected_traces = []

            for ch in unique_channels:
                selected_traces.append(next(tr for tr in st if tr.stats.channel == ch))
            st = Stream(selected_traces)

            trim_st = st.copy()
            sta_picks = picks_idx[picks_idx['station'] == ii[2]]
            p_picks = sta_picks.loc[sta_picks['phase'] == 'P']
            s_picks = sta_picks.loc[sta_picks['phase'] == 'S']
    #         print(len(p_picks),len(s_picks))




    #         if len(p_picks) == 0:
    #             continue 
    #         print('This is after the p_pick continue statement')
            print(trim_st)

            for iax in range(len(trim_st)):
                print(iax)
                sampling_rate = trim_st[iax].stats.sampling_rate
                trim_st = trim_st.normalize()

                if len(p_picks)>0:
                    tp = UTCDateTime(p_picks.iloc[0]['time_pick']) - otime + 30
                    i1 = int((tp-5)*sampling_rate)
                    i2 = int((tp+15)*sampling_rate)
                elif len(s_picks)>0:
                    ts = UTCDateTime(s_picks.iloc[0]['time_pick']) - otime + 30
                    i1 = int((ts-10)*sampling_rate)
                    i2 = int((ts+10)*sampling_rate)
                else:
                    print(f"WARNING: No pick time for {ii[1]}.{ii[2]}.{channel} on {otime}.")

                offsets1 = ii[3]
                try: 
                    wave = trim_st[iax].data
                    wave = wave / (np.nanmax(wave[i1:i2], axis=-1)*10)
                except:
                    continue 

    #             print(trim_st[iax].stats.sampling_rate)
                axs[iax].plot(trim_st[iax].times(), wave * scaling_factor + offsets1, 
                              color='black', label=f"{trim_st[iax].stats.channel}", alpha=0.7, lw=0.5)
    #             axs[iax].plot(trim_st[iax].times(), wave * 30 + offsets1, color='black', label=f"{trim_st[iax].stats.channel}", alpha=0.7, lw=0.5)

    #             axs[iax].text(xlim[-1] + 2,   offsets1, 
    #                               [ii[2]], fontsize=8, verticalalignment='bottom')

                if len(p_picks) > 0:
                    axs[iax].vlines(UTCDateTime(p_picks.iloc[0]['time_pick']) - otime + 30, offsets1 - (1/35) * scaling_factor, 
                                    offsets1 + (1/35) * scaling_factor, color='r')
                if len(s_picks) > 0:
                    axs[iax].vlines(UTCDateTime(s_picks.iloc[0]['time_pick']) - otime + 30, offsets1 - (1/35) * scaling_factor, 
                                    offsets1 + (1/35) * scaling_factor, color='b')
            texts.append([ii[2],ii[3]])


    #     print(max_y,min_y)
        chs = ['2','1','Z']
        for iax in range(3):
            for i, ii in enumerate(texts):
                offsets1 = ii[1]
                axs[iax].text(max_x + 0.5, offsets1, 
                                      [ii[0]], fontsize=8, verticalalignment='bottom')
            axs[iax].legend(chs[iax],loc='upper right', handlelength=0)
            axs[iax].set_ylim([min_y,max_y])
            axs[iax].set_xlim([min_x,max_x])
            axs[iax].grid(alpha=0.5)
        fig.supxlabel('Time [sec]', y=0.07)
        fig.supylabel('Distance [km]')
        fig.suptitle(f"{title}: Origin Time={otime}, \n Latitude={round(event[event['idx']==idx]['latitude'].values[0], 2)}, Longtitude={round(event[event['idx']==idx]['longitude'].values[0], 2)}, Depth={round(event[event['idx']==idx]['depth'].values[0], 2)}", y=1)

        m = Basemap(projection='merc', llcrnrlat=40, urcrnrlat=50, llcrnrlon=-130, urcrnrlon=-120, resolution='i', ax=axs[3])
        m.drawcoastlines()
        m.drawcountries()
        m.drawstates()
        m.drawmapboundary()
        m.drawparallels(np.arange(40, 51, 1), labels=[1,0,0,0])
        m.drawmeridians(np.arange(-130, -119, 1), labels=[0,0,0,1])
        x, y = m(event[event['idx']==idx]['longitude'].values[0], event[event['idx']==idx]['latitude'].values[0])
        m.plot(x, y, 'ro', markersize=9)
        axs[3].set_title('Event Location')
        
        fig.savefig(p, format='pdf')  

    p.close()

### Specify the latitudes and longitudes

In [ ]:
new_events = pd.read_csv('../data/datasets_2014/new_events.csv')

In [ ]:
idx = new_events[new_events['station']=='J25B']['idx'].values
idx

In [ ]:
new_events = new_events[new_events["idx"].isin(idx)]
new_events

In [ ]:
new_events_specific_lat_lon = new_events.loc[(new_events['latitude']>46)&(new_events['latitude']<47.5)&(new_events['longitude']<-124)&(new_events['longitude']>-126)]
new_events_specific_lat_lon

In [ ]:
# new_events = new_events_specific_lat_lon.loc[(new_events_specific_lat_lon['depth']>1)&(new_events_specific_lat_lon['depth']<40)]
new_events = new_events_specific_lat_lon.loc[new_events_specific_lat_lon['picks']>=6][0:30]
new_events

### Histogram: Depths of events

In [ ]:
# Plot the histogram of the number of picks for the matched events
plt.figure()
bins = np.linspace(0,50,25)
plt.hist(new_events['depth'],bins=bins)
plt.xlabel('Depth (km)')
plt.ylabel('Number of Events')
plt.title('Histogram of the depths of the events in the cluster at ~46.5$^\circ$ N')

### Plot HH?

In [ ]:
# parameters
mycatalog= mycatalog
mycatalog_picks=mycatalog_picks
networks= all_picks_networks
channel= "HH?"
idx_sta= 50
title= "Events matched"
fig_title= "events_matched.png"
ylim= [0,300]
xlim= [30,45]

for idx in new_events['idx']:
    subplots_cluster_scale_p(idx,mycatalog,mycatalog_picks,networks,channel,idx_sta,title,fig_title,ylim,xlim)

### Plot BH?

In [ ]:
# parameters
mycatalog= mycatalog
mycatalog_picks=mycatalog_picks
networks= all_picks_networks
channel= "BH?"
idx_sta= 50
title= "Events matched"
fig_title= "events_matched.png"
ylim= [0,300]
xlim= [30,45]

for idx in new_events['idx']:
    subplots_cluster_scale_p(idx,mycatalog,mycatalog_picks,networks,channel,idx_sta,title,fig_title,ylim,xlim)

### Plot both HH? and BH?

In [ ]:
new_events['datetime'] = pd.to_datetime(new_events['datetime'], utc = True)
new_events

In [ ]:
# parameters for subplots_cluster_scale_p
mycatalog= mycatalog
mycatalog_picks=mycatalog_picks
networks= all_picks_networks
channel= "?H?"
idx_sta= 50
title= "Events matched"
fig_title= "events_matched.png"

for idx in new_events['idx']:
    subplots_cluster_scale_p(idx,new_events,mycatalog_picks,networks,channel,idx_sta,title,fig_title)

In [ ]:
# parameters for subplots_cluster_scale
mycatalog= mycatalog
mycatalog_picks=mycatalog_picks
networks= all_picks_networks
channel= "?H?"
idx_sta= 50
title= "Events matched"
fig_title= "new_events_plots.pdf"

subplots_cluster_scale(new_events,mycatalog_picks,networks,channel,idx_sta,title,fig_title)

In [ ]:
# Plot the histogram of the number of picks for the matched events
new_events['time'] = pd.to_datetime(new_events['time'])
year1 = 2012
time1 = datetime(year=year1, month=1, day=1)
time2 = datetime(year=year1 + 1, month=1, day=1)
time_bins = pd.date_range(start=time1, end=time2, freq='5D')
plt.figure()
plt.hist(new_events['time'], bins=time_bins)
plt.xlabel('Days')
plt.ylabel('Number of Events')
plt.title('Histogram for the frequency of the events in the cluster at ~46.5$^\circ$ N')
plt.xticks(rotation=45)  # Optional: Rotate x-axis labels for better readability
plt.show()

In [ ]:
import matplotlib 
from matplotlib import pyplot as plt 
from matplotlib.backends.backend_pdf import PdfPages 

# customizing runtime configuration stored 
# in matplotlib.rcParams 
plt.rcParams["figure.figsize"] = [7.00, 3.50] 
plt.rcParams["figure.autolayout"] = True

fig1 = plt.figure() 
plt.plot([17, 45, 7, 8, 7], color='orange') 

fig2 = plt.figure() 
plt.plot([13, 25, 1, 6, 3], color='blue') 

Fig3 = plt.figure() 
plt.plot([22, 11, 2, 1, 23], color='green') 


def save_image(filename): 
	
	# PdfPages is a wrapper around pdf 
	# file so there is no clash and create 
	# files with no error. 
	p = PdfPages(filename) 
	
	# get_fignums Return list of existing 
	# figure numbers 
	fig_nums = plt.get_fignums() 
	figs = [plt.figure(n) for n in fig_nums] 
	
	# iterating over the numbers in list 
	for fig in figs: 
		
		# and saving the files 
		fig.savefig(p, format='pdf') 
	
	# close the object 
	p.close() 

# name your Pdf file 
filename = "multi_plot_image.pdf"

# call the function 
save_image(filename) 


## Plot the cluster events at around 43.25&deg; N, 124.25&deg; W using the plotting functions 

In [ ]:
new_events_specific_lat_lon = unmatched_events_mycatalog2morton_and_anss.loc[(unmatched_events_mycatalog2morton_and_anss['latitude']>43.0)&(unmatched_events_mycatalog2morton_and_anss['latitude']<43.3)&(unmatched_events_mycatalog2morton_and_anss['longitude']<-124.25)&(unmatched_events_mycatalog2morton_and_anss['longitude']>-124.75)]
new_events_specific_lat_lon

In [ ]:
new_events = new_events_specific_lat_lon.loc[new_events_specific_lat_lon['picks']>5]
new_events

### Plot HH?

In [ ]:
# parameters
mycatalog= mycatalog
mycatalog_picks=mycatalog_picks
networks= all_picks_networks
channel= "HH?"
idx_sta= 50
title= "Events matched"
fig_title= "events_matched.png"
ylim= [0,300]
xlim= [20,150]

for idx in new_events['idx']:
    subplots_cluster_scale_p(idx,mycatalog,mycatalog_picks,networks,channel,idx_sta,title,fig_title,ylim,xlim)

### Plot BH?

In [ ]:
# parameters
mycatalog= mycatalog
mycatalog_picks=mycatalog_picks
networks= all_picks_networks
channel= "BH?"
idx_sta= 50
title= "Events matched"
fig_title= "events_matched.png"
ylim= [0,300]
xlim= [20,150]

for idx in new_events['idx']:
    subplots_cluster_scale_p(idx,mycatalog,mycatalog_picks,networks,channel,idx_sta,title,fig_title,ylim,xlim)

## Calculate SNRs

In [ ]:
all_picks = pd.read_csv('../data/datasets_2014/all_picks_2014.csv')
all_pick_assignments = pd.read_csv('../data/datasets_2014/all_pick_assignments_2014.csv')

In [ ]:
def calc_snr(all_picks,all_pick_assignments):
    """ 
    This function calculates the SNRs for each station in each event.
    
    Inputs:
    1. The all_pick.csv file from the 2_format_pick2associate file.
    2. The all_pick_assignments.csv file from the 3_association file.
    
    Oututs:
    The new all_pick_assignments_snr file with the additional SNR column.
    """
    
    # Create the list of networks
    all_picks_networks = all_picks['station_network_code'].drop_duplicates()
    list_networks = list(all_picks_networks)
    networks = ','.join(all_picks_networks)
    
    
    
    # Define the clients 
    client_waveform = WaveformClient()
    client2 = Client("IRIS")
    client_ncedc = Client('NCEDC')
    
    all_pick_assignments['datetime'] = pd.to_datetime(all_pick_assignments['time'], utc = True)

    
    # Define parameters
    percentile=98
    
    # Create empty lists
    snr_list = []
        
    # Make sure if a station for an event has more than 1 P or S pick
    for idx in all_pick_assignments['idx'].drop_duplicates():
        # Define parameters
        otime = UTCDateTime(str(all_pick_assignments[all_pick_assignments['idx'] == idx]["datetime"].values[0]))


        # Create empty lists
        networks_stas = []

        # Plot the earthquake moveout for one of the unmatched events for all stations 
    #     event = mycatalog
        pick_idx = all_pick_assignments.loc[all_pick_assignments['idx']==idx]
        pick_sta = np.unique(pick_idx['station'])
        
    #     distances = []
    #     max_dist = 10
    #     min_dist = 0
        for station in pick_sta:

            sta_inv = client2.get_stations(network=networks,
                                           station=station, channel="?H?", 
                                           starttime=otime - 1e8, endtime=otime + 1e8,level="response")
            if len(sta_inv) == 0:
                print(f'No inventory for station {station}. Skipping.')
                continue

            network = sta_inv[0].code
    #         slat = sta_inv[0][0].latitude
    #         slon = sta_inv[0][0].longitude
    #         olat = event.loc[event['idx']==idx, 'latitude'].values[0]
    #         olon = event.loc[event['idx']==idx, 'longitude'].values[0]

    #         dis1 = locations2degrees(olat, olon, slat, slon)
    #         dist = degrees2kilometers(dis1)
    # #         if max_dist < dist:
    # #             max_dist = dist

    # #         if min_dist > dist:
    # #             min_dist = dist

            networks_stas.append([network,station])
        
   
        events = all_pick_assignments[all_pick_assignments['idx']==idx]
        for i in networks_stas:
            events1 = events[events['station']==i[1]]
            p_picks = events1[events1['phase']=='P']
            s_picks = events1[events1['phase']=='S']
            

            if len(p_picks)>0 and len(s_picks)>0:
                print(p_picks['datetime'].values,s_picks['datetime'].values)
                p_pick_time = UTCDateTime(str(p_picks['datetime'].values[0]))
                s_pick_time = UTCDateTime(str(s_picks['datetime'].values[0]))
                
                starttime_st = UTCDateTime(p_pick_time)-timedelta(seconds=120)
                endtime_st = UTCDateTime(p_pick_time)+timedelta(seconds=120)
                
                starttime_noise = UTCDateTime(p_pick_time)-timedelta(seconds=8)
                endtime_noise = UTCDateTime(p_pick_time)
                
                starttime_signal = UTCDateTime(s_pick_time)-timedelta(seconds=1)
                endtime_signal = UTCDateTime(s_pick_time)+timedelta(seconds=2)
                
                print(starttime_noise,endtime_noise)
            
                if i[0] in ['NC', 'BK']:
                # Query waveforms
                    st = client_ncedc.get_waveforms(network=i[0], station=i[1],
                                                    location="*", channel="?HZ",starttime=starttime_st,
                                                    endtime=endtime_st)

                elif i[0] in networks: 
                    st = client_waveform.get_waveforms(network=i[0], station=i[1],
                                                       channel='?HZ',starttime=starttime_st, endtime=endtime_st)

                else: 
                    st =  Stream()
                    print(f"WARNING: No data for {ii[1]}.{ii[2]}.{channel} on {otime}.")    
                    continue

        #         print(f"len(st):{len(st)}")
        #         print(st)

                # Skip empty traces
                if len(st) == 0:
                    continue
                    
                print(f'First st print:{st}')
                # Create a new stream
                _st = Stream()
                # Check for HH and BH channels presence
                has_HH = bool(st.select(channel="HH?"))
                has_BH = bool(st.select(channel="BH?"))

                # Apply selection logic based on channel presence
                if has_HH and has_BH:
                    # If both HH and BH channels are present, select only HH
                    _st += st.select(channel="HH?")
                elif has_HH:
                    # If only HH channels are present
                    _st += st.select(channel="HH?")
                elif has_BH:
                    # If only BH channels are present
                    _st += st.select(channel="BH?")

                _st.merge(fill_value='interpolate') # fill gaps if there are any.

                print(f'Second st print:{_st}')
            
                noise = _st.copy().trim(starttime=starttime_noise,endtime=endtime_noise)    
                signal = _st.copy().trim(starttime=starttime_signal,endtime=endtime_signal) 
                
                print(f"P and S pick times:{p_pick_time} and {s_pick_time}")
                print(f"Stream start and end times:{starttime_st} and {endtime_st}")
                print(f"Noise start and end times:{starttime_noise} and {endtime_noise}")
                print(f"Signal start and end times:{starttime_signal} and {endtime_signal}")
                
                print(f'Noise:{noise}')
                print(f'Signal:{signal}')

                noise_abs = np.percentile(abs(noise[0].data),percentile)
                signal_abs = np.percentile(abs(signal[0].data),percentile)

                snr = 20 * np.log10((signal_abs/noise_abs))

                snr_list.append(snr)
                
            if len(p_picks)>0 and len(s_picks)==0:
                
                print(p_picks['datetime'].values,s_picks['datetime'].values)
                p_pick_time = UTCDateTime(str(p_picks['datetime'].values[0]))
#                 s_pick_time = UTCDateTime(str(s_picks['datetime'].values[0]))

                starttime_st = UTCDateTime(p_pick_time)-timedelta(seconds=120)
                endtime_st = UTCDateTime(p_pick_time)+timedelta(seconds=120)
                
                starttime_noise = UTCDateTime(p_pick_time)-timedelta(seconds=8)
                endtime_noise = UTCDateTime(p_pick_time)
                
                starttime_signal = UTCDateTime(p_pick_time)+timedelta(seconds=1)
                endtime_signal = UTCDateTime(p_pick_time)+timedelta(seconds=4)
                
            
                if i[0] in ['NC', 'BK']:
                # Query waveforms
                    st = client_ncedc.get_waveforms(network=i[0], station=i[1],
                                                    location="*", channel="?HZ",starttime=starttime_st, 
                                                    endtime=endtime_st)

                elif i[0] in networks: 
                    st = client_waveform.get_waveforms(network=i[0], station=i[1],
                                                       channel='?HZ',starttime=starttime_st, endtime=endtime_st)

                else: 
                    st =  Stream()
                    print(f"WARNING: No data for {ii[1]}.{ii[2]}.{channel} on {otime}.")    
                    continue

        #         print(f"len(st):{len(st)}")
        #         print(st)

                # Skip empty traces
                if len(st) == 0:
                    continue
                print(f'First st print:{st}')
                # Create a new stream
                _st = Stream()
                # Check for HH and BH channels presence
                has_HH = bool(st.select(channel="HH?"))
                has_BH = bool(st.select(channel="BH?"))

                # Apply selection logic based on channel presence
                if has_HH and has_BH:
                    # If both HH and BH channels are present, select only HH
                    _st += st.select(channel="HH?")
                elif has_HH:
                    # If only HH channels are present
                    _st += st.select(channel="HH?")
                elif has_BH:
                    # If only BH channels are present
                    _st += st.select(channel="BH?")

                _st.merge(fill_value='interpolate') # fill gaps if there are any.

                print(f'Second st print:{_st}')
                
                
                    

                noise = _st.copy().trim(starttime=starttime_noise,endtime=endtime_noise)    
                signal = _st.copy().trim(starttime=starttime_signal,endtime=endtime_signal) 
                
                print(f"P pick time:{p_pick_time}")
                print(f"Stream start and end times:{starttime_st} and {endtime_st}")
                print(f"Noise start and end times:{starttime_noise} and {endtime_noise}")
                print(f"Signal start and end times:{starttime_signal} and {endtime_signal}")

                print(f'Noise:{noise}')
                print(f'Signal:{signal}')

                noise_abs = np.percentile(abs(noise[0].data),percentile)
                signal_abs = np.percentile(abs(signal[0].data),percentile)

                snr = 20 * np.log10((signal_abs/noise_abs))

                snr_list.append(snr)
                    
            if len(p_picks)==0 and len(s_picks)>0:
                print(p_picks['datetime'].values,s_picks['datetime'].values)
#                 p_pick_time = UTCDateTime(str(p_picks['datetime'].values))
                s_pick_time = UTCDateTime(str(s_picks['datetime'].values[0]))
    
                starttime_st = UTCDateTime(s_pick_time)-timedelta(seconds=120)
                endtime_st = UTCDateTime(s_pick_time)+timedelta(seconds=120)
                
                starttime_noise = UTCDateTime(s_pick_time)-timedelta(seconds=8)
                endtime_noise = UTCDateTime(s_pick_time)
                
                starttime_signal = UTCDateTime(s_pick_time)
                endtime_signal = UTCDateTime(s_pick_time)+timedelta(seconds=3)
                
                print(starttime_noise,endtime_noise)
            
                if i[0] in ['NC', 'BK']:
                # Query waveforms
                    st = client_ncedc.get_waveforms(network=i[0], station=i[1],
                                                    location="*", channel="?HZ",starttime=starttime_st, 
                                                    endtime=endtime_st)

                elif i[0] in networks: 
                    st = client_waveform.get_waveforms(network=i[0], station=i[1],
                                                       channel='?HZ',starttime=starttime_st, endtime=endtime_st)

                else: 
                    st =  Stream()
                    print(f"WARNING: No data for {ii[1]}.{ii[2]}.{channel} on {otime}.")    
                    continue

        #         print(f"len(st):{len(st)}")
        #         print(st)

                # Skip empty traces
                if len(st) == 0:
                    continue
                    
                print(f'First st print:{st}')
                # Create a new stream
                _st = Stream()
                # Check for HH and BH channels presence
                has_HH = bool(st.select(channel="HH?"))
                has_BH = bool(st.select(channel="BH?"))

                # Apply selection logic based on channel presence
                if has_HH and has_BH:
                    # If both HH and BH channels are present, select only HH
                    _st += st.select(channel="HH?")
                elif has_HH:
                    # If only HH channels are present
                    _st += st.select(channel="HH?")
                elif has_BH:
                    # If only BH channels are present
                    _st += st.select(channel="BH?")

                _st.merge(fill_value='interpolate') # fill gaps if there are any.

                print(f'Second st print:{_st}')

            
                noise = _st.copy().trim(starttime=starttime_noise,endtime=endtime_noise)    
                signal = _st.copy().trim(starttime=starttime_signal,endtime=endtime_signal) 
                
                print(f"S pick time:{s_pick_time}")
                print(f"Stream start and end times:{starttime_st} and {endtime_st}")
                print(f"Noise start and end times:{starttime_noise} and {endtime_noise}")
                print(f"Signal start and end times:{starttime_signal} and {endtime_signal}")
                
                print(f'Noise:{noise}')
                print(f'Signal:{signal}')

                noise_abs = np.percentile(abs(noise[0].data),percentile)
                signal_abs = np.percentile(abs(signal[0].data),percentile)

                snr = 20 * np.log10((signal_abs/noise_abs))

                snr_list.append(snr)
            
    all_assignments_picks['snr']=snr_list
     
    return snr_list

In [ ]:
snr_list = calc_snr(all_picks,all_pick_assignments)

In [ ]:
snr_list

In [ ]:
client_waveform = WaveformClient()

p_pick_time = '2014-01-02T07:40:02.642533Z'

starttime_st = UTCDateTime(p_pick_time)-timedelta(seconds=120)
endtime_st = UTCDateTime(p_pick_time)+timedelta(seconds=120)

# starttime_st = UTCDateTime('2011-01-03T00:00:0.000000Z')
# endtime_st = UTCDateTime('2011-01-03T12:59:59.000000Z')

print(f'Requested start and end times:{starttime_st} and {endtime_st}')


st = client_waveform.get_waveforms(network='CN', station='BTB',
                                       channel='HHZ',starttime=starttime_st, endtime=endtime_st)
print(f'Actual start and end times: {st[0].stats.starttime} and {st[0].stats.endtime}')
